# Code Specialization

To be fast, Julia needs to **specialize** code, that is compile specific native versions of the code. **The better the specialization the faster the code!** In the following we will investigate how Julia achieves good code specialization while retaining the power of generic programming.

## Just Ahead of Time (JAOT) Compilation

![](../../static/from_source_to_native.png)
 

**AST = Abstract Syntax Tree**

**IR = Intermediate Representation**

**SSA = Static Single Assignment**

**[LLVM](https://de.wikipedia.org/wiki/LLVM) = Low Level Virtual Machine**

## Specialization

**Julia specializes on the types of function arguments**, i.e. Julia compiles efficient machine code for the given input types, **when a function is called for the first time**.

If it is called again, the already existing machine code is reused, until we call the function with different input types.


In [ ]:
func(x, y) = 2x + y

In [ ]:
x = [1.2, 3.4, 5.6] # Vector{Float64}
y = [0.4, 0.7, 0.9] # Vector{Float64}

@time func(x, y);
@time func(x, y);

**First call:** compilation + running the code

**Second call:** running the code


In [ ]:
@time func(x, y);

If one of the input types changes, Julia compiles a new specialization of the function!


In [ ]:
typeof(x)

In [ ]:
x = [1, 3, 5]

In [ ]:
typeof(x)

In [ ]:
@time func(x, y); # Vector{Int64}, Vector{Float64}
@time func(x, y);

We now have two efficient native codes in the cache: one for all `Vector{Float64}` inputs and another one for `Vector{Int64}` as the first and `Vector{Float64}` as the second argument type.

In [ ]:
using MethodAnalysis

In [ ]:
methods(func)

In [ ]:
methodinstances(func)

## Introspection

(*But I really want to see what happens!*)

We can inspect the code at all transformation stages with a bunch of macros:

<img src="../../static/julia_introspection_macros.png" width=350px>

### Code Lowering

Compiler optimisation is a very hard task, to make the compilers life easier it should be given 'simple' code.

In Julia 'simple' means [static single-assignment form](https://en.wikipedia.org/wiki/Static_single-assignment_form):

> In compiler design, static single assignment form (often abbreviated as SSA form or simply SSA) is a property of an intermediate representation (IR) that requires each variable to be assigned exactly once and defined before it is used.
>
> ...
>
> One can expect to find SSA in a compiler for Fortran, C or C++ ...

This transformation from source code to SSA form is called **lowering**, and the SSA form is called **lowered code**.

In [ ]:
function basic_condition(bool::Bool)
    if bool
        return 0
    else
        return 1
    end
end

In [ ]:
@code_lowered basic_condition(true)

In [ ]:
# Increase verbosity with `debuginfo=:source`
@code_lowered debuginfo=:source basic_condition(true)

In [ ]:
function basic_loop()
    a = 0
    for i in [1, 2, 3]
        a += i
    end
    return a
end

In [ ]:
@code_lowered debuginfo=:source basic_loop()

- `#N` refers to [basic blocks](https://en.wikipedia.org/wiki/Basic_blockhttps://en.wikipedia.org/wiki/Basic_block) of code
  - Blocks are shown on the left with `|` characters outlining their span
- `%N` refers to single static assignment (SSA) valuesrefer to single static assignment (SSA) values, when a previous SSA value is used, it's referenced by an `SSAValue` and printed as `%N`
- `@_N` refers to temporary variables

In [ ]:
function nextfib(n)
    a, b = one(n), one(n)
    while b < n
        a, b = b, a + b
    end
    return b
end

In [ ]:
@code_lowered debuginfo=:source nextfib(1)

### Type Inference

The above lowered code now starts to get **specialised**: argument types and any explicit annotations are used to infer the types of all SSA variables (where/if possible), and that information is then used to specialise the function calls:

In [ ]:
@code_typed debuginfo=:source nextfib(1.0)

In [ ]:
@code_typed debuginfo=:source nextfib(1)

Note the specialisation on the types, instead of generic `+` and `>`, now specific `add_float`/`add_int` are used!

Whereas in Python:

```ipython
In [1]: import dis

In [2]: def nextfib(n):
   ...:     a, b = 1, 1
   ...:     while b < n:
   ...:         a, b = b, a + b
   ...:     return b
   ...: 

In [3]: dis.dis(nextfib)
  2           0 LOAD_CONST               1 ((1, 1))
              2 UNPACK_SEQUENCE          2
              4 STORE_FAST               1 (a)
              6 STORE_FAST               2 (b)

  3           8 LOAD_FAST                2 (b)
             10 LOAD_FAST                0 (n)
             12 COMPARE_OP               0 (<)
             14 POP_JUMP_IF_FALSE       19 (to 38)

  4     >>   16 LOAD_FAST                2 (b)
             18 LOAD_FAST                1 (a)
             20 LOAD_FAST                2 (b)
             22 BINARY_ADD
             24 ROT_TWO
             26 STORE_FAST               1 (a)
             28 STORE_FAST               2 (b)

  3          30 LOAD_FAST                2 (b)
             32 LOAD_FAST                0 (n)
             34 COMPARE_OP               0 (<)
             36 POP_JUMP_IF_TRUE         8 (to 16)

  5     >>   38 LOAD_FAST                2 (b)
             40 RETURN_VALUE

In [4]: def add(a, b):
    ...:     return a.__add__(b)
    ...: 

In [5]: dis.dis(add)
  2           0 LOAD_FAST                0 (a)
              2 LOAD_METHOD              0 (__add__)
              4 LOAD_FAST                1 (b)
              6 CALL_METHOD              1
              8 RETURN_VALUE
```

Types are not known, so the correct functions have to be found **each time** an operation is done.

Whereas Julia can compile the code once for given input types and then directly call the required function.

This crucial process is known as **type inference** and its success is the basis for a good specialization (i.e. performant native code as a result). It will concern us in much more detail tomorrow.

### LLVM IR

The next step is to go from lowered typed code to LLMV IR.

Julia uses the LLVM compiler framework, which is also used by Rust, Swift, Kotlin, and other languages.

'IR' means [Intermediary Representation](https://en.wikipedia.org/wiki/Intermediate_representation):

> An intermediate representation (IR) is the data structure or code used internally by a compiler or virtual machine to represent source code. An IR is designed to be conducive to further processing, such as optimization and translation

In [ ]:
@code_llvm basic_condition(true)  # dump_module=true shows the 'full' ir

In [ ]:
@code_llvm nextfib(1)

### Native Code

In [ ]:
@code_native debuginfo=:source nextfib(1)  # binary=true to see the raw binary code

Let's compare this to integer input.


In [ ]:
@code_native debuginfo=:source nextfib(1.0)

## How Important is Specialization?

Let's try to estimate the performance gain by specialization, we can do this by breaking the compilation process by throwing away type information.

This way Julia will act, roughly, in the same way as Python: it has to work out what can be done to a variable every single time it encounters it. We can do this by storing the variables in a `Vector{Any}`.

First, let's write the same `nextfib` function in Python and benchmark it:

```ipython
In [1]: def nextfib(n):
   ...:     a, b = 1, 1
   ...:     while b < n:
   ...:         a, b = b, a + b
   ...:     return b
   ...: 

In [2]: %timeit nextfib(100_000)
951 ns ± 7.39 ns per loop (mean ± std. dev. of 7 runs, 1,000,000 loops each)
```

In [ ]:
using BenchmarkTools
using PythonCall

@pyexec """
global nextfib

def nextfib(n):
     a, b = 1, 1
     while b < n:
         a, b = b, a + b
     return b
"""

@benchmark @pyexec "nextfib(100_000)"

Now, for reference, here is the standard implementation in Julia:

In [ ]:
function nextfib(n)
    a, b = one(n), one(n)
    while b < n
        a, b = b, a + b
    end
    return b
end

In [ ]:
@benchmark nextfib(100_000)

And the broken version, which:

- Throws away type information by storing variables in a `Vector{Any}`
- Force enables bounds-checks for situations where they could be optimised away (e.g. the 3-element vector)
- Disables specialisation on the argument `n`

In [ ]:
function nextfib_bad(n)
    vars::Vector{Any} = [1, 1, n]
    while vars[2] < vars[3]
        vars[1], vars[2] = vars[2], vars[1] + vars[2]
    end
    return vars[2]
end

In [ ]:
@benchmark nextfib_bad(100_000)

This is (on my computer) *almost* the same as the Python version!

In [ ]:
# @code_typed nextfib_bad(100)
# @code_native nextfib_bad(100)

## Types vs Values

In high performance computing, compilation time (order of seconds or minutes) is typically neglectable compared to the actual time it takes to perform the computation (readily on the orders of hours/days/weeks). Therefore, we generally want to optimize for runtime efficiency even if this means that compilation time goes up by a reasonable amount.

**Julia specializes on input types and not values!**

Primarily it is **type information** that is used by the compiler to specialize code. (There are special techniques like, e.g., constant propagation and others that we are neglecting here.)

(Very) roughly speaking, the more information there is in *type space* (e.g. in type parameters) the higher the likelihood that the compiler produces fast and efficient code.

As before, here is a Python benchmark:

```ipython
In [1]: import numpy as np

In [2]: A = np.random.rand(10, 10)

In [3]: B = np.random.rand(10, 10)

In [4]: %timeit A + B
507 ns ± 4.51 ns per loop (mean ± std. dev. of 7 runs, 1,000,000 loops each)
```

In [ ]:
np = pyimport("numpy")

A = np.random.rand(10, 10)
B = np.random.rand(10, 10);

In [ ]:
@btime $A + $B;

In [ ]:
A = rand(10, 10);
B = rand(10, 10);
@btime $A + $B;

In [ ]:
typeof(A)

In [ ]:
size(A)

In [ ]:
size(typeof(A)) # the size of A isn't type information

In [ ]:
using StaticArrays

In [ ]:
A = @SMatrix rand(10, 10);
B = @SMatrix rand(10, 10);

In [ ]:
typeof(A)

In [ ]:
size(typeof(A)) # the size of A is type information!

In [ ]:
@btime $A + $B;

**StaticArrays.jl**

```
============================================
    Benchmarks for 3×3 Float64 matrices
============================================
Matrix multiplication               -> 5.9x speedup
Matrix multiplication (mutating)    -> 1.8x speedup
Matrix addition                     -> 33.1x speedup
Matrix addition (mutating)          -> 2.5x speedup
Matrix determinant                  -> 112.9x speedup
Matrix inverse                      -> 67.8x speedup
Matrix symmetric eigendecomposition -> 25.0x speedup
Matrix Cholesky decomposition       -> 8.8x speedup
Matrix LU decomposition             -> 6.1x speedup
Matrix QR decomposition             -> 65.0x speedup
```

### Why not always use static arrays then?!

By putting more information in the type you are putting more stress on the compiler to optimize things.

Specifically, if static arrays are too big compile time can explode or the compiler might just give up and fall back to an inefficient default version.

Generally speaking, static arrays are only useful as small fixed-size arrays.

In [ ]:
# # should take (much) longer to compile and the speedup should be gone as well
# # if it isn't, increase N a little bit
# N = 50
# M = rand(N,N);
# Mstatic = SMatrix{N,N}(M);

# @btime $Mstatic + $Mstatic;
# @btime $M + $M;

### Dispatch and Specialization

Having a reasonable amount of information encoded in the type domain isn't only useful to help the compiler (specialization) but also for dispatching to the most specific (and therefore hopfully most performant) method of a function.

**Types drive both specialization and multiple dispatch!**

In this sense, multiple dispatch is essentially the first step of the specialization process where Julia chooses between different implementations.

#### Example: Determinant of a 2x2 matrix

Let's say your task would be to write a function computing the determinant of a 2x2 matrix. How would you implement it?

Probably you'd say, well I know the formula for computing the determinant of a 2x2 matrix! Let's just implement it.

In Python:

```ipython
In [1]: import numpy as np

In [2]: M = np.array([[1, 2], [3, 4]])

In [3]: def det_2x2(X):
   ...:     return X[0, 0] * X[1, 1] - X[0, 1] * X[1, 0]
   ...: 

In [4]: %timeit det_2x2(M)
502 ns ± 10.5 ns per loop (mean ± std. dev. of 7 runs, 1,000,000 loops each)
```

And for Julia:

In [ ]:
det_2x2(X) = X[1, 1] * X[2, 2] - X[1, 2] * X[2, 1]

In [ ]:
M = [1 2; 3 4]

In [ ]:
det_2x2(M)

In [ ]:
@btime det_2x2(M);

Let's see how Julia's built-in `det` function compares to our algorithm, first in Numpy:

```ipython
In [6]: %timeit np.linalg.det(M)
4.75 µs ± 59.9 ns per loop (mean ± std. dev. of 7 runs, 100,000 loops each)
```

Almost 10x slower than the hand-written version! And for Julia:

In [ ]:
using LinearAlgebra

det(M)

In [ ]:
@btime det(M);

20x slower!

The reason isn't just that the compiler doesn't just know the size of the matrix from its type but also that [the code it considers](https://github.com/JuliaLang/julia/blob/release-1.8/stdlib/LinearAlgebra/src/generic.jl#L1544-L1550) (selected by the dispatch mechanism) is too general to compete with our implementation in `det_2x2`.

Let's now move the size information to the type domain and see how things change.

In [ ]:
using StaticArrays
S = @SMatrix [1 2; 3 4]

In [ ]:
@btime det($S);

Note that it is super faster because StaticArrays.jl provides [a hand-coded version](https://github.com/JuliaArrays/StaticArrays.jl/blob/master/src/det.jl#L10-L12), similar to our `det_2x2` above, which gets selected because of the size information in the type.

The (tiny) speed difference compared to our own `det_2x2` is only due to bounds checking and matrix vs linear indexing.

In [ ]:
det_2x2_optimized(X) = X[1] * X[4] - X[3] * X[2]
@btime det_2x2_optimized($M);

## Are Explicit Type Annotations Necessary?

Fortan/C require them, are they required in Julia?

In [ ]:
function my_function(x)
    y = rand()
    z = rand()
    x + y + z
end

function my_function_typed(x::Int)::Float64
    y::Float64 = rand()
    z::Float64 = rand()
    x + y + z
end

Nope! Julia's type inference is powerful. Specifying types **is not** necessary for best performance.

In [ ]:
@btime my_function(10);
@btime my_function_typed(10);

Annotating types explicitly can serve a purpose.

* Enforce conversions
* Very rarely: help the compiler infer types in tricky situations

However, more often than not it is an indication of suboptimal code design. (It also makes functions much less generic and reusable!)

# Core messages of this Notebook

* **A function is compiled when called for the first time** with a given set of argument types.
* The are **multiple compilation steps** which can be inspected through macros like `@code_warntype`.
* **Code specialization** based on the types of all of the input arguments is important for speed.
* Critical information can be moved to the **type domain** for better dispatch and specialization.
* In virtually all cases, **explicit type annotations are irrelevant for performance**.

# References

- https://github.com/carstenbauer/JuliaHLRS22/blob/main/Day1/3_specialization.ipynb
- https://docs.julialang.org/en/v1/devdocs/ast/
- https://juliadebug.github.io/JuliaInterpreter.jl/stable/ast/
- https://stackoverflow.com/questions/43453944/what-is-the-difference-between-code-native-code-typed-and-code-llvm-in-julia
- https://tenthousandmeters.com/blog/python-behind-the-scenes-4-how-python-bytecode-is-executed/